In [2]:
import pandas as pd
import json

## Identifying the number of Suburbs to extract the require coordinates

In [3]:
# import the perth housing price 
perth_house_df = pd.read_csv("../Dataset/perth_housing_price_2021.csv")
perth_house_df

ADDRESS           SUBURB    PRICE  BEDROOMS  BATHROOMS  \
0           1 Acorn Place       South Lake   565000         4          2   
1             1 Addis Way            Wandi   365000         3          2   
2         1 Ainsley Court          Camillo   287000         3          1   
3         1 Albert Street         Bellevue   255000         2          1   
4            1 Aman Place        Lockridge   325000         4          1   
...                   ...              ...      ...       ...        ...   
33646      9C Gold Street  South Fremantle  1040000         4          3   
33647      9C Pycombe Way      Westminster   410000         3          2   
33648      9D Pycombe Way      Westminster   427000         3          2   
33649     9D Shalford Way       Girrawheen   295000         3          1   
33650  9E Margaret Street          Midland   295000         3          1   

       GARAGE  LAND_AREA  FLOOR_AREA  BUILD_YEAR  CBD_DIST  \
0         2.0        600         160      2003.0     18300   
1         2.0        351         139      2013.0     26900   
2         1.0        719          86      1979.0     22600   
3         2.0        651          59      1953.0     17900   
4         2.0        466         131      1998.0     11200   
...       ...        ...         ...         ...       ...   
33646     2.0        292         245      2013.0     16100   
33647     2.0        228         114      2015.0      9600   
33648     2.0        261         112      2016.0      9600   
33649     2.0        457          85      1974.0     12600   
33650     2.0        296          95      1979.0     16700   

                    NEAREST_STN  NEAREST_STN_DIST  MONTH_SOLD  YEAR_SOLD  \
0      Cockburn Central Station              1800           9       2018   
1               Kwinana Station              4900           2       2019   
2               Challis Station              1900           6       2015   
3               Midland Station              3600           7       2018   
4            Bassendean Station              2000          11       2016   
...                         ...               ...         ...        ...   
33646         Fremantle Station              1500           3       2016   
33647          Stirling Station              4600           2       2017   
33648          Stirling Station              4600           2       2017   
33649           Warwick Station              4400          10       2016   
33650           Midland Station              1700           5       2016   

       POSTCODE   LATITUDE   LONGITUDE  \
0          6164 -32.115900  115.842450   
1          6167 -32.193470  115.859554   
2          6111 -32.120578  115.993579   
3          6056 -31.900547  116.038009   
4          6054 -31.885790  115.947780   
...         ...        ...         ...   
33646      6162 -32.064580  115.751820   
33647      6061 -31.867055  115.841403   
33648      6061 -31.866890  115.841418   
33649      6064 -31.839680  115.842410   
33650      6056 -31.882163  116.014755   

                                       NEAREST_SCH  NEAREST_SCH_DIST  \
0                      Lakeland Senior High School          0.828339   
1                                   Atwell College          5.524324   
2                     Kelmscott Senior High School          1.649178   
3                     Swan View Senior High School          1.571401   
4                                    Kiara College          1.514922   
...                                            ...               ...   
33646                  Christian Brothers' College          1.430350   
33647  John Septimus Roe Anglican Community School          1.679644   
33648  John Septimus Roe Anglican Community School          1.669159   
33649                Girrawheen Senior High School          0.358494   
33650                             La Salle College          1.055564   

       NEAREST_SCH_RANK  
0                   NaN  
1                 129.0  

In [4]:
# group by as suburb together and extract the suburb name
suburb_grp = perth_house_df.groupby("SUBURB").count()
suburb_list = suburb_grp.index
suburb_list

Index(['Alexander Heights', 'Alfred Cove', 'Alkimos', 'Anketell', 'Applecross',
       'Ardross', 'Armadale', 'Ascot', 'Ashby', 'Ashfield',
       ...
       'Wilson', 'Winthrop', 'Woodbridge', 'Woodlands', 'Woodvale', 'Wooroloo',
       'Wungong', 'Yanchep', 'Yangebup', 'Yokine'],
      dtype='object', name='SUBURB', length=321)

### Import geojson file to match with the suburb data have

In [5]:
with open("../Dataset/suburb-10-wa.geojson", "r") as f:
  suburb_coordinate = json.load(f)

suburb_coordinate


{'type': 'FeatureCollection',
 'features': [{'type': 'Feature',
   'geometry': {'type': 'Polygon',
    'coordinates': [[[115.65091361, -21.10517973],
      [115.65008472, -21.10309861],
      [115.65041556, -21.0997586],
      [115.65155667, -21.09815556],
      [115.65352693, -21.09859306],
      [115.6544864, -21.09993944],
      [115.65482028, -21.10115666],
      [115.65442832, -21.10380861],
      [115.65514139, -21.10484444],
      [115.65647389, -21.1054975],
      [115.65703972, -21.10675557],
      [115.65654917, -21.10782444],
      [115.65490166, -21.10885889],
      [115.65290306, -21.10870418],
      [115.65182444, -21.10813111],
      [115.65093972, -21.10638556],
      [115.65091361, -21.10517973]]]},
   'properties': {'lc_ply_pid': '4811',
    'dt_create': '2010-02-18Z',
    'dt_retire': None,
    'loc_pid': 'WA1702',
    'wa_localit': '2017-11-01Z',
    'wa_local_1': None,
    'wa_local_2': 'MARDIE',
    'wa_local_3': None,
    'wa_local_4': None,
    'wa_local_5': 'G'

In [8]:
# creating geojson file
geojson_feature = []

# identify the location of the data
coordinate_data = suburb_coordinate["features"]
# putting suburbs that founded into a list to ensure every suburbs are captured
suburb_founded = []

for suburb in suburb_list:
    for n in coordinate_data:
        # locate the suburb name for each coordinate_data
        dum_suburb = n["properties"]["wa_local_2"].title()
        if suburb == dum_suburb:
            # create temp dict for storing all coordinate and suburb name
            dum_dict = {}
            # putting the coordinates or geometry into temp dict
            dum_dict["geometry"] = n["geometry"]
            # putting suburb name into properties
            dum_dict["properties"] = {"suburb_name" : dum_suburb}

            # typical feature for type
            dum_dict["type"] = "Feature"
            
            # append the temp dict into geojson feature list
            geojson_feature.append(dum_dict)
            suburb_founded.append(suburb)

# putting all dict and list into geojson
geojson_file = {"type": "FeatureCollection", "features" : geojson_feature}
geojson_file

{'type': 'FeatureCollection',
 'features': [{'geometry': {'type': 'Polygon',
    'coordinates': [[[115.85460474, -31.83589904],
      [115.85452563, -31.83457701],
      [115.85395161, -31.83305216],
      [115.85257589, -31.83062903],
      [115.8522786, -31.82923262],
      [115.85257706, -31.82796858],
      [115.85398171, -31.82559144],
      [115.85432615, -31.82416198],
      [115.85435984, -31.82095804],
      [115.86086115, -31.82096783],
      [115.86723536, -31.82111098],
      [115.87282489, -31.82098236],
      [115.87723677, -31.82102561],
      [115.87702692, -31.82397442],
      [115.8770081, -31.83503655],
      [115.87468594, -31.83461135],
      [115.86798987, -31.83255712],
      [115.86579022, -31.83224146],
      [115.86362987, -31.83256901],
      [115.86248089, -31.83305586],
      [115.85833614, -31.83542496],
      [115.85631908, -31.83588147],
      [115.85460474, -31.83589904]]]},
   'properties': {'suburb_name': 'Alexander Heights'},
   'type': 'Feature'},
 

In [7]:
# checking and ensure that every suburbs in the dataframe have coordinates data
for suburb in suburb_founded:
    if suburb not in suburb_list:
        print(suburb)

In [37]:
with open("./output/Perth_suburb.geojson", "w") as outfile:
    json.dump(geojson_file, outfile)